# MTB++ output analysis

##Reading output of the MTB++

In [1]:
import pandas as pd

# LR
MTBpp_Logistic_Regression = pd.read_csv("Logistic Regression.csv")

# RF
MTBpp_Random_Forest = pd.read_csv("Random Forest.csv")



## List of phenotypes

In [2]:
phenotypes = [
    "Amikacin",
    "Bedaquiline",
    "Clofazimine",
    "Delamanid",
    "Ethambutol",
    "Ethionamide",
    "Isoniazid",
    "Kanamycin",
    "Levofloxacin",
    "Linezolid",
    "Moxifloxacin",
    "Rifampicin",
    "Rifabutin",
    "RIA",
    "AMG",
    "FQS"
]


# LR analysis

In [3]:
def calculate_counts_and_ratio(df,phenotypes):
    # Initialize dictionaries to store counts
    resistant_counts = {}
    susceptible_counts = {}

    # Iterate over the columns and count occurrences
    for column in phenotypes:
        resistant_counts[column] = df[df[column] == "Resistant"].shape[0]
        susceptible_counts[column] = df[df[column] == "Susceptible"].shape[0]
    # Calculate the ratio of "Resistant" to the total number of "Resistant" and "Susceptible" for each phenotype
    ratio_counts = {
        phenotype: round(resistant_counts.get(phenotype, 0) / (resistant_counts.get(phenotype, 0) + susceptible_counts.get(phenotype, 0)), 4)
        for phenotype in phenotypes
    }


    table_data = [["Phenotypes", "Resistant", "Susceptible", "Ratio"]]

    # Create a new DataFrame with counts and ratio
    for phenotype in phenotypes:
        row = [
            phenotype,
            resistant_counts.get(phenotype, 0),
            susceptible_counts.get(phenotype, 0),
            ratio_counts.get(phenotype, 0)
        ]
        table_data.append(row)

    table_df = pd.DataFrame(table_data[1:], columns=table_data[0])

    return table_df

# Calculate counts and ratio for both dataframes
MTB_LR = calculate_counts_and_ratio(MTBpp_Logistic_Regression,phenotypes)
MTB_RF = calculate_counts_and_ratio(MTBpp_Random_Forest,phenotypes)

# Concatenate the dataframes horizontally (side by side) with super columns
result_df = pd.concat([MTB_LR, MTB_RF], axis=1)

# Print the united output
result_df.to_csv("MTB++_united_results.csv", index=False)

## Heatmaps

confusion_matrix_plotter create a sub ax for each confusion matrix that is possbile between 2 antibiotics, it is based on jaccard index of the antibiotics

In [4]:
def confusion_matrix_plotter(input_list, ax=None):
    import matplotlib.pyplot as plt
    import numpy as np
    from matplotlib.colors import LinearSegmentedColormap
    from matplotlib.patches import Rectangle
    import copy
    # Define your 2x2 matrix
    matrix = np.array(input_list).reshape(2, 2)
    max_number=matrix[0,0]+matrix[1,0]+matrix[0,1]
    # Use the top-left element for color mapping and set other elements to a value that corresponds to white
    copied_matrix=copy.copy(matrix)
    top_left_value = matrix[0, 0]

    copied_matrix.fill(top_left_value)  # Set all elements to a value outside the color mapping range
    copied_matrix[0, 0] = top_left_value  # Restore the top-left element

    # Define a custom colormap
    colors = [(1, 1, 1), (1, 0, 0)]  # First color is white, second is red
    n_bins = 100000  # Number of bins
    cmap_name = "custom_cmap"
    custom_cmap = LinearSegmentedColormap.from_list(cmap_name, colors, N=n_bins)

    # If ax is not provided, create a new subplot
    if ax is None:
        fig, ax = plt.subplots()

    # Create a heatmap-like plot of the matrix within the specified subplot
    im = ax.imshow(copied_matrix, cmap=custom_cmap, interpolation='nearest', vmin=0, vmax=max_number)

    # Set X and Y tick positions and labels for both axes
    ax.set_xticks([0, 1])
    ax.set_yticks([0, 1])
    ax.set_xticklabels(['R', 'S'], fontsize=40)
    ax.set_yticklabels(['R', 'S'], fontsize=40)

    # Add lines to separate the matrix cells
    ax.axhline(y=0.5, color='black', linewidth=2)
    ax.axvline(x=0.5, color='black', linewidth=2)

    # Create a black border rectangle around the 'im'
    rect = Rectangle((-.5, -.5), 2, 2, linewidth=2, edgecolor='black', facecolor='none', transform=ax.transData)
    ax.add_patch(rect)

    # Add numeric labels to each element of the matrix
    for i in range(2):
        for j in range(2):
            ax.text(j, i, f'{matrix[i][j]}', ha='center', va='center', color='black', fontsize=40)

    return im


The next function will plot the jaccard index for the input dataframes

In [5]:
def Jaccard_index_plotter(input_df, output_name):
  import copy
  df=copy.copy(input_df)
# Initialize a 2D list to store the counts
  count_matrix = []

  # Iterate through each phenotype pair to create a confusion matrix (it's a 1-D list for each pair of antibiotics )
  for phenotype_i in phenotypes:
      row = []
      for phenotype_j in phenotypes:
          # Calculate the counts for the pair (i, j)
          count_susceptible_both = sum((df[phenotype_i] == "Susceptible") & (df[phenotype_j] == "Susceptible"))
          count_susceptible_resistant = sum((df[phenotype_i] == "Susceptible") & (df[phenotype_j] == "Resistant"))
          count_resistant_susceptible = sum((df[phenotype_i] == "Resistant") & (df[phenotype_j] == "Susceptible"))
          count_resistant_both = sum((df[phenotype_i] == "Resistant") & (df[phenotype_j] == "Resistant"))

          row.append((count_resistant_both, count_resistant_susceptible , count_susceptible_resistant,count_susceptible_both ))

      count_matrix.append(row)



  import matplotlib.pyplot as plt
  import numpy as np
  from matplotlib.patches import Rectangle

  # Assuming you already have the count_matrix and phenotypes defined

  fig, ax = plt.subplots(figsize=(80, 80))

  for i in range(len(phenotypes)):
      for j in range(len(phenotypes)):
          if i > j:
              counts = count_matrix[i][j]
              sub_ax = fig.add_subplot(len(phenotypes), len(phenotypes), i * len(phenotypes) + j + 1)
              confusion_matrix_plotter(counts, ax=sub_ax)

              # Set phenotype names as labels on the first column and last row
              if j == 0:
                  sub_ax.set_ylabel(phenotypes[i], fontsize=50)
              if i == len(phenotypes) - 1:
                  sub_ax.set_xlabel(phenotypes[j], fontsize=50)

  # Hide the original tick labels and ticks
  plt.setp(ax, xticks=[], yticks=[], xticklabels=[], yticklabels=[])

  plt.tight_layout()
  plt.savefig('{}.jpg'.format(output_name), format='jpg',dpi=70, bbox_inches='tight')
  plt.show()
  plt.close()

In [ ]:
Jaccard_index_plotter(MTBpp_Logistic_Regression,"LR_Jaccard_index")
Jaccard_index_plotter(MTBpp_Random_Forest,"RF_Jaccard_index")

In [8]:
import pandas as pd

# Assuming you have two dataframes named MTBpp_Logistic_Regression and MTBpp_Random_Forest
# with the relevant data

phenotypes = [
    "Amikacin",
    "Bedaquiline",
    "Clofazimine",
    "Delamanid",
    "Ethambutol",
    "Ethionamide",
    "Isoniazid",
    "Kanamycin",
    "Levofloxacin",
    "Linezolid",
    "Moxifloxacin",
    "Rifampicin",
    "Rifabutin",
    "RIA",
    "AMG",
    "FQS"
]

# Create a dictionary to store the counts
resistance_counts = {}

# Iterate through each phenotype
for phenotype in phenotypes:
    # Count the cases where both dataframes have "Resistant" for the current phenotype
    RR = ((MTBpp_Logistic_Regression[phenotype] == "Resistant") &
             (MTBpp_Random_Forest[phenotype] == "Resistant")).sum()

    RS = ((MTBpp_Logistic_Regression[phenotype] == "Resistant") &
             (MTBpp_Random_Forest[phenotype] == "Susceptible")).sum()

    SR = ((MTBpp_Logistic_Regression[phenotype] == "Susceptible") &
             (MTBpp_Random_Forest[phenotype] == "Resistant")).sum()

    # Assign the count to the specific key in the dictionary
    resistance_counts[phenotype] = RR/(1+RS+SR)
    print (phenotype)
    print (RR/(RR+RS+SR))
    print ("--------")
# Print the dictionary with counts
print(resistance_counts)


Amikacin
0.9545175169022742
--------
Bedaquiline
0.0
--------
Clofazimine
0.020491803278688523
--------
Delamanid
0.0
--------
Ethambutol
0.7137128072445019
--------
Ethionamide
0.7104350146784094
--------
Isoniazid
0.9348752282410225
--------
Kanamycin
0.728167808219178
--------
Levofloxacin
0.9120545868081881
--------
Linezolid
0.01948051948051948
--------
Moxifloxacin
0.6682808716707022
--------
Rifampicin
0.8493647912885662
--------
Rifabutin
0.8525963149078727
--------
RIA
0.853641933287951
--------
AMG
0.7049248747913188
--------
FQS
0.5597971965404116
--------
{'Amikacin': 20.706666666666667, 'Bedaquiline': 0.0, 'Clofazimine': 0.020833333333333332, 'Delamanid': 0.0, 'Ethambutol': 2.491869918699187, 'Ethionamide': 2.451197053406998, 'Isoniazid': 14.332814930015552, 'Kanamycin': 2.6745283018867925, 'Levofloxacin': 10.32618025751073, 'Linezolid': 0.019736842105263157, 'Moxifloxacin': 2.012150668286756, 'Rifampicin': 5.6343115124153496, 'Rifabutin': 5.779399837793998, 'RIA': 5.82804